In [ ]:
import glob
import zipfile
import yaml
import os
from sklearn.metrics.pairwise import cosine_similarity
import numpy as np
import torchvision.transforms as transforms
import pandas as pd
import numpy as np
from PIL import Image
import torch
from google.colab import files

# EDA

In [ ]:
#Child, Adult 분포 알아보기
import os
import pandas as pd
import seaborn as sns
path = './labels/'
file_list = os.listdir(path)
a = ' '
for file in file_list:
    filepath = path + '/' + file
    with open(filepath, 'r') as labels:
        a += labels.read()
lines = a.strip().split('\n')
data = [line.split() for line in lines]
# 데이터 프레임 생성
columns = ['child', 'x', 'y', 'w', 'h']
df = pd.DataFrame(data, columns=columns)
df['child'] = df['child'].astype(int)
# Child Adult 히스토그램 그리기
ax = sns.countplot(x = df['child'], data=df, palette='Set3')
for p in ax.patches:
    height = p.get_height()
    ax.text(p.get_x() + p.get_width() / 2, height + 3, height, ha = 'center', size = 9)
# ax.set_ylim(5, 10)
plt.show()

# Dataset

In [ ]:
import json
import cv2
import os
from tqdm import tqdm
from traitlets.traitlets import Unicode

def data_cook(folder_name):

    #folder 내 확장자명이 json 혹은 mp4인 파일들을 리스트업 후 중복 제거하여 리스트로 저장
    file_names = list(set([dir.split('.')[0] for dir in os.listdir(folder_name) if (dir.split('.')[1] == 'json') or dir.split('.')[1] =='mp4' ]))
    print(file_names)
    # 파일명들을 순회하며 모든 동영상과 그에 대응하는 제이슨 파일에 접근!
    for file_name in tqdm(file_names):
        #확장자명 제외한 파일 이름만 입력

        json_dir = folder_name + "/" + file_name + '.json'
        video_dir = folder_name + "/" + file_name+'.mp4'

        ### txt 저장부############################

        #제이슨 읽어오기
        with open(json_dir, "r",encoding='utf-8') as json_file:
            json_data = json.load(json_file)
            #id값 임시 저장용 dictionary
            id_dict = {}
            #출력용 빈문자열 생성
            #비디오 해상도 튜플로 저장 : (가로픽셀수 , 세로픽셀수)
            resolution = (json_data['video']['resolution'][0], json_data['video']['resolution'][1])
            #id별로 연령대 정보 저장
            for person in json_data['categories']:
                id_dict[person['id']] = person['age']

            #프레임별 불러오기
            frame_dict = {}  # 키값 : 프레임넘버 / 벨류값 : 데이터(라벨,x,y,w,h \n 라벨,x,y,w,h \n 라벨,x,y,w,h \n ...)
            for annotation in json_data['annotations']:

                #현재 annotation이 해당하는 프레임정보 저장
                frame_num = annotation['frame']
                #세자리 숫자로 이루어진 문자열로 변환 (예. 001, 002, 003, ~ 540)
                frame_digit = str(frame_num + 1000)[1:]

                #프레임 내 id 불러와 저장
                id = annotation['id']
                #아까 임시저장한 딕셔너리에서 id에 해당하는 age값 불러와 라벨로 저장
                if id_dict[id] =='child':
                    label = 1
                else:
                    label = 0

                # bbox 불러오기(우리 제이슨에는 min-max픽셀 형식이다.)
                xmin, ymin, xmax, ymax = annotation['bbox'][0], annotation['bbox'][1], annotation['bbox'][2], annotation['bbox'][3]
                # darknet형식으로 변환하기.(x,y,w,h로 표현하고 전체 이미지의 비율로 표현)
                x = (xmax+xmin) / (2*resolution[0])
                y = (ymax+ymin) / (2*resolution[1])
                w = (xmax-xmin) / resolution[0]
                h = (ymax-ymin) / resolution[1]
                # darknet 데이터 형식으로 객체는 줄바꿈으로 구분! 객체 내 요소는 label,x,y,w,h 다섯개이며 띄어쓰기로 구분
                output = '{label} {x} {y} {w} {h}\n'.format(label = label, x = x, y = y, w = w, h = h)

                #딕셔너리에 프레임별 저장
                # 해당 프레임넘버가 딕셔너리에 키값으로 존재하지 않는다면,
                if frame_digit not in frame_dict:
                    #새 키값에 벨류로 할당
                    frame_dict[frame_digit] = output
                # 해당 프레임넘버가 딕셔너리에 이미 키값으로 존재한다면
                else:
                    # 딕셔너리 벨류에 output을 이어쓴다.(문자열)
                    frame_dict[frame_digit] += output

            #프레임별 딕셔너리 데이터를 각기 다른 텍스트 파일로 저장
            for frame_number in frame_dict:
                with open('{file_name}_F{frame_number}.txt'.format(file_name=file_name, frame_number=frame_number), 'w') as f:
                    f.write(str(frame_dict[frame_number]))


        #print('[',file_name,']','의 txt파일 저장 완료 :',len(frame_dict),'개 파일')

        ### 동영상 저장부############################

        # 오브젝트가 없는 프레임은 txt저장이 되지 않았다. 이미지도 그에 맞춰서 저장해야한다.
        # 이미지가 저장된 프레임의 번호를 아래와 같이 int값으로 변환해 리스트로 바꿔주자.
        frame_list = [int(num_str) for num_str in list(frame_dict.keys())]

        #(테스트용) 영상 내 최초 오브젝트 등장 프레임
        # first_obj = min(frame_list)
        # first_obj_sec = int(180 * (first_obj/540))
        #print("최초 obj 등장은 영상({}.mp4) 내 {}분, {}초경 입니다. ".format(file_name, first_obj_sec//60, first_obj_sec%60))

        current_frame = 0   # 세자리 숫자를 iii 형식으로 쓰기 위한 잔머리... 예시 > 20을 020, 128을 128, 7을 007

        cap = cv2.VideoCapture(video_dir)      # 동영상 캡처 객체 생성
        if cap.isOpened():                      # 캡처 객체 초기화 확인
            while True:
                check, img = cap.read()           # 다음 프레임 읽기
                if check:                        # 프레임 읽기 정상이라면
                    if current_frame in frame_list:
                        cv2.waitKey(1)             # 333ms 지연(40fps로 가정)
                        cv2.imwrite("{video_name}_F{frame_number}.jpg".format(video_name = file_name,frame_number = str(1000 + current_frame)[1:]), img)
                        print("저장완료 : {video_name}_F{frame_number}.jpg".format(video_name = file_name,frame_number = str(1000 + current_frame)[1:]))
                else:
                    print(f'{current_frame} : 이 프레임을 읽을 수가 업써')
                current_frame += 1
                if current_frame == 539:
                    print('마지막 프레임 도착! : ', current_frame,'번')
                    break

        else:
            print("비디오가 안열리는뎁쇼.")          # 캡처 객체 초기화 실패
        cap.release()                           # 캡쳐 자원 반납(비우기)

In [ ]:
df = {
    'area' : [],
    'file_name' : [],
    'kids' : []
}
path = '1.Training'

for folder_name in glob.glob(path+'/*'):
    for file_name in glob.glob(folder_name+'/*'):
        count = 0
        with open(file_name, "r",encoding = "UTF-8" ) as json_file:
            json_data = json.load(json_file)

            for person in json_data['categories']:
                if person['age'] == 'child':
                    count += 1
            if count == 0:
                continue
            else:
                df['area'].append(folder_name.split('\\')[-1])
                df['file_name'].append(file_name.split('\\')[-1])
                df['kids'].append(count)

kids_only = pd.DataFrame(df)

#Training

In [ ]:
import glob
import zipfile
import yaml
import os
import random
from sklearn.model_selection import train_test_split
label_file = zipfile.ZipFile('/content/drive/MyDrive/Object_Detection/labels.zip')
label_file.extractall('/content/data/train/labels')
img_file = zipfile.ZipFile('/content/drive/MyDrive/Object_Detection/images.zip')
img_file.extractall('/content/data/train/images')
root_dir = '/content/data'
root_train_dir = '/content/data/train'
images = glob.glob('/content/data/train/images/*.jpg')  # 수정된 이미지 경로
labels = glob.glob('/content/data/train/labels/*.txt')  # 수정된 검증 라벨 경로
train_images, valid_images, train_labels, valid_labels = train_test_split(images, labels, test_size=0.2, random_state=42)
# train.txt 만들기
with open(os.path.join(root_train_dir, "train.txt"), 'w') as f:
    f.write('\n'.join(train_images) + '\n')
with open(os.path.join(root_train_dir, "valid.txt"), 'w') as f:
    f.write('\n'.join(valid_images) + '\n')
yaml_data = {"names":['Adult', 'Child'],  # 클래스 이름
             "nc":2,  # 클래스 수
             "path":root_dir,  # root 경로
             "train":os.path.join(root_train_dir, "train.txt"),  # train.txt 경로
             "val":os.path.join(root_train_dir, "valid.txt" ),  # valid.txt 경로
             }
with open(os.path.join(root_dir, "custom.yaml"), "w") as f:
    yaml.dump(yaml_data, f)
!git clone https://github.com/ultralytics/yolov5
%cd yolov5
!pip install -r requirements.txt
%cd /content/yolov5/
!python train.py --img 640 --batch 64 --epochs 50 --data /content/data/custom.yaml --weights yolov5s.pt yolv5l --name guide_yolov5s_results
!python train.py --img 640 --batch 64 --epochs 30 --data /content/data/custom.yaml --weights /content/yolov5/runs/train/guide_yolov5s_results/weights/best.pt --name guide_yolov5s_results
!python train.py --img 640 --batch 64 --epochs 50 --data /content/data/custom.yaml --weights /content/finalbest.pt --name guide_yolov5s_results
!python3 detect.py --source /content/2021-09-08_16-18-00_wed_sunny_out_sa-bt_C0091_F220.jpg --weights /content/yolov5/runs/train/guide_yolov5s_results/weights/best.pt

#Inference

##STAGE1

In [ ]:
pip install -r https://raw.githubusercontent.com/ultralytics/yolov5/master/requirements.txt

In [ ]:
model_1 = torch.hub.load('ultralytics/yolov5', 'custom', path='/content/drive/MyDrive/Object_Detection/finalbest.pt')

Using cache found in /root/.cache/torch/hub/ultralytics_yolov5_master
YOLOv5 🚀 2023-8-9 Python-3.10.12 torch-2.0.1+cu118 CPU

Fusing layers... 
Model summary: 157 layers, 7015519 parameters, 0 gradients, 15.8 GFLOPs
Adding AutoShape... 


In [ ]:
def stage_1(model, frame):
    with torch.no_grad():
        results = model(frame)
        crops = results.crop(save=False)

    crop_img_list = []
    bbox_list = []
    child_list = []

    for crop in crops:
        left, top, right, bottom = int(crop['box'][0]), int(crop['box'][1]), int(crop['box'][2]), int(crop['box'][3])
        img_crop = crop['im']

        if crop['label'].split()[0] == 'Child' :
            child_or_not = 1
        else:
            child_or_not = 0

        bbox_list.append((left, top, right, bottom))
        crop_img_list.append(img_crop)
        child_list.append(child_or_not)

    return bbox_list, crop_img_list, child_list

##STAGE2

In [ ]:
%cd /content

/content


In [ ]:
def zip_files(input_files, output_zip):
    with zipfile.ZipFile(output_zip, 'w') as zipf:
        for file in input_files:
            zipf.write(file)

def unzip_file(zip_file_path, extract_to):
    with zipfile.ZipFile(zip_file_path, 'r') as zip_ref:
        zip_ref.extractall(extract_to)

def get_all_files_in_folder(folder_path, file_list):
    for root, dirs, files in os.walk(folder_path):
        for file in files:
            file_path = os.path.join(root, file)
            file_list.append(file_path)
    return file_list

# if __name__ == "__main__":
#     # 압축할 파일들의 경로 및 파일명 리스트
#     input_files = ['/content/val_dataset.txt',
#                    '/content/train_dataset.txt',
#                    '/content/test_dataset.txt',
#                    '/content/main.py',
#                    '/content/inception_iccv.py',
#                    '/content/datasets.py',
#                    '/content/bn_inception-52deb4733.pth',
#                    '/content/25.pth.tar',
#                    ]
#     get_all_files_in_folder('/content/test_images', input_files)
#     get_all_files_in_folder('/content/train_images', input_files)
#     get_all_files_in_folder('/content/val_images', input_files)
#     get_all_files_in_folder('/content/yolo_images', input_files)

#     # 압축 파일의 경로 및 파일명
#     output_zip = "./parparparparpar_cpu.zip"

#     # 파일 압축
#     zip_files(input_files, output_zip)


In [ ]:
!gdown 1CVc-UJnIciPRnMUN7UBRKdJPwBCGR1_I
unzip_file('/content/parparparparpar_cpu.zip', '/')
!rm parparparparpar_cpu.zip

Downloading...
From: https://drive.google.com/uc?id=1CVc-UJnIciPRnMUN7UBRKdJPwBCGR1_I
To: /content/parparparparpar_cpu.zip
100% 226M/226M [00:00<00:00, 273MB/s]


In [ ]:
import numpy as np
import torch
import torch.nn as nn
from datasets import Get_Dataset
import inception_iccv as models
import pandas as pd
from tqdm import tqdm


def write_log(log):
    print(log)
    with open("./log.txt", 'a', encoding='utf8') as log_f:
        log_f.write(log + "\n")

def modelfor2():
    args = {
        'approach' : 'inception_iccv',
        'resume' : '25.pth.tar',
        'start_epoch' : 0,
        'lr' : 0.0001,
        'weight_decay' : 0.0005,
        'attr_num' : 43
        }

    if torch.cuda.is_available():
        device = torch.device('cuda')
    else:
        print('[CUDA unavailable]')
        device = torch.device('cpu')

    model = models.inception_iccv(pretrained=False, num_classes=args['attr_num'])
    model = torch.nn.DataParallel(model).to(device)

    write_log('Number of model parameters: {}'.format(
        sum([p.data.nelement() for p in model.parameters()])))
    write_log('')
    if args['resume']:
        if os.path.isfile(args['resume']):
            write_log("=> loading checkpoint '{}'".format(args['resume']))
            checkpoint = torch.load(args['resume'], map_location=device)
            args['start_epoch'] = checkpoint['epoch']
            best_accu = checkpoint['best_accu']
            model.load_state_dict(checkpoint['state_dict'])
            write_log("=> loaded checkpoint '{}' (epoch {})"
                    .format(args['resume'], checkpoint['epoch']))
        else:
            write_log("=> no checkpoint found at '{}'".format(args['resume']))

    optimizer = torch.optim.Adam(model.parameters(), lr=args['lr'],
                                    betas=(0.9, 0.999),
                                    weight_decay=args['weight_decay'])
    _, _, _, attr_num, description = Get_Dataset('foottraffic', 'inception_iccv')

    return model, optimizer, attr_num, description


In [ ]:
normalize = transforms.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225])
transform = transforms.Compose([
        transforms.Resize(size=(256, 128)),
        transforms.ToTensor(),
        normalize
        ])

In [ ]:
%cd /content/

/content


In [ ]:
import torchvision.transforms as transforms
import pandas as pd
import numpy as np
from PIL import Image
import torch

model_2, optimizer, attr_num, description = modelfor2()

def stage_2(model, crop_list) :
    input = torch.stack([transform(Image.fromarray(np.array(crop).astype(np.uint8)).convert('RGB')) for crop in crop_list])
    y = model(input)
    if type(y) == type(()) or type(y) == type([]):
        y = torch.max(torch.max(torch.max(y[0], y[1]), y[2]), y[3])
    output = torch.sigmoid(y.data).cpu().numpy()
    output = np.where(output > 0.5, 1, 0)
    original_df = pd.DataFrame(output, columns = description)
    return original_df, y, output

[CUDA unavailable]
[CUDA unavailable]
[CUDA unavailable]
[CUDA unavailable]
Number of model parameters: 16147440

=> loading checkpoint '25.pth.tar'
=> loaded checkpoint '25.pth.tar' (epoch 25)


In [ ]:
sex_list          = ['male', 'female']
age_list          = ['child', 'teenager', 'adult', 'senior']
top_type_list     = ['long_sleeve', 'short_sleeve', 'sleeveless', 'onepice']
top_color_list    = ['red', 'orange', 'yellow', 'green', 'blue',
                    'purple', 'pink', 'brown', 'white', 'grey', 'black']
bottom_type_list  = ['long_pants', 'short_pants', 'skirt', 'none_type']
bottom_color_list = ['red', 'orange', 'yellow', 'green', 'blue', 'purple', 'pink',
                    'brown', 'white', 'grey', 'black']

# for i, nm in enumerate(img_name):
#     li = [nm]
#     li.append(sex_list[np.argmax(output[:,0:2], axis= 1)[i]])
#     li.append(age_list[np.argmax(output[:,2:6], axis= 1)[i]])
#     li.append(top_type_list[np.argmax(output[:,6:10], axis= 1)[i]])
#     li.append(top_color_list[np.argmax(output[:,10:21], axis= 1)[i]])
#     li.append(bottom_type_list[np.argmax(output[:,21:25], axis= 1)[i]])
#     li.append(bottom_color_list[np.argmax(output[:,25:36], axis= 1)[i]])


def clothing(i, output) : # i = index
    li = []
    li.append(top_type_list[np.argmax(output[:,6:10], axis= 1)[i]])
    li.append(top_color_list[np.argmax(output[:,10:21], axis= 1)[i]])
    li.append(bottom_type_list[np.argmax(output[:,21:25], axis= 1)[i]])
    li.append(bottom_color_list[np.argmax(output[:,25:36], axis= 1)[i]])
    return li


## Post Processing

### 함수정의

In [ ]:
total_annotations = []
total_children = []

def tracking(pre_frame_ids, pre_frame_vecs, pre_centers,
             post_bbox_list, post_frame_vecs, current_frame, output, child_list,
             distance_rate=3, similar_threshold = 0.921, speed_threshold = 0.3) :

    global person_num
    global total_annotations
    global total_children
    annotations = []
    children_anot = []
    red_bboxes = []

    if current_frame == 0 :
        post_centers = np.array([[(right + left)/2 ,bottom]for left, bottom, right, top in post_bbox_list])
        post_frame_ids = []
        speeds = []
        for i in range(output.shape[0]) :
            speed = np.array([0,0]) # Default speed
            person_id = f"Person_{person_num}"
            person_num += 1
            post_frame_ids.append(person_id) #현재 frame의 id를 저장해야
            speeds.append(speed)
            clothes = clothing(i, output)

            annotations.append({'id' : person_id,
                                'Frame' :current_frame,
                                'bbox' : post_bbox_list[i],
                                'speed' : speed,
                                "clothes" : clothes})

        #연산의 편의를 위한 array 변환
        post_frame_ids = np.array(post_frame_ids)

        child_idxs = np.where(np.array(child_list)  == 1)
        distances_from_children = np.sqrt(np.sum((post_centers[child_idxs] - post_centers[:, np.newaxis]) ** 2, axis=2))
        distances_from_children = distances_from_children.T

        for i, child_idx in enumerate(child_idxs[0]):
            kid_meter = post_bbox_list[child_idx][3] - post_bbox_list[child_idx][1]
            distance_threshold = kid_meter * distance_rate
            near_idxs = np.where((distances_from_children[i] < distance_threshold) &(distances_from_children[i] > 0))[0]
            near_ids = post_frame_ids[near_idxs]
            clothes = clothing(child_idx, output)
            company = []

            children_anot.append({'id' : post_frame_ids[child_idx],
                                    'Frame' : current_frame,
                                    'bbox' : post_bbox_list[child_idx],
                                    'near_ids' : near_ids,
                                    'company' : company,
                                    "clothes" : clothes
                                    })

    else:
        post_centers = np.array([[(right + left)/2 ,bottom]for left, top, right, bottom in post_bbox_list])

        # similarity : all post_frame_vecs vs pre_frame_vecs
        # (i,j)는 post_frame의 i번째 object와 pre_frame의 j번째 object 사이의 유사도를 의미
        similarity_matrix = cosine_similarity(post_frame_vecs.detach().numpy(), pre_frame_vecs.detach().numpy())

        # distances : all pre_centers vs post_centers
        # (i,j)는 post_frame의 i번째 box와 pre_frame의 j번째 box 사이의 거리를 의미
        post_pre_distances = np.sqrt(np.sum((post_centers[:, np.newaxis, :] - pre_centers) ** 2, axis=2))

        #보정치 : 거리가 0이면 1, 1에 가까이 가면 무한대로 발산
        post_pre_distances = post_pre_distances / (frame_width**2+frame_height**2)**(1/2)
        comp = -np.log(1 + 1e-7 - post_pre_distances) + 1

        # features와 거리를 모두 고려한 유사도
        similarity_matrix = similarity_matrix / comp

        # 유력한 id끼리 매칭
        max_indices = np.argmax(similarity_matrix, axis = 1)
        pre_idxs = np.where(similarity_matrix[np.arange(similarity_matrix.shape[0]), max_indices] >= similar_threshold, max_indices, -1)

        post_frame_ids = []
        speeds = []
        for post_idx, pre_idx in enumerate(pre_idxs) :
            speed = np.array([0,0]) # Default speed
            if pre_idx != -1 :
                person_id = pre_frame_ids[pre_idx]
                speed = post_centers[post_idx] - pre_centers[pre_idx] #Calculate speed
            else:
                person_id = f"Person_{person_num}"
                person_num += 1

            post_frame_ids.append(person_id) #현재 frame의 ids를 저장해야 (순서 중요)
            speeds.append(speed)
            clothes = clothing(post_idx, output)
            annotations.append({'id' : person_id,
                                'Frame' :current_frame,
                                'bbox' : post_bbox_list[post_idx],
                                'speed' : speed,
                                "clothes" : clothes})

        #연산의 편의를 위한 array 변환
        post_frame_ids = np.array(post_frame_ids)

        # child's index, distances from children
        # row가 아이, columns이 모든 객체
        child_idxs = np.where(np.array(child_list)  == 1)
        distances_from_children = np.sqrt(np.sum((post_centers[child_idxs] - post_centers[:, np.newaxis]) ** 2, axis=2))
        distances_from_children = distances_from_children.T

        # speed ratio로 company를 구해봅시다
        for i, child_idx in enumerate(child_idxs[0]):
            kid_meter = post_bbox_list[child_idx][3] - post_bbox_list[child_idx][1]
            distance_threshold = kid_meter * distance_rate
            near_idxs = np.where((distances_from_children[i] < distance_threshold) &(distances_from_children[i] > 0))[0]
            near_ids = post_frame_ids[near_idxs]
            company = []
            if not np.array_equal(near_idxs, np.array([])):
                for j, near_idx in enumerate(near_idxs):
                    speed_similarity = cosine_similarity([speeds[near_idx]], [speeds[child_idx]])
                    if speed_similarity > speed_threshold : #방향 유사도
                        company.append(near_ids[j])
            clothes = clothing(child_idx, output)
            warning = 0
            if not company :
                warning = 1
                red_bboxes.append(post_bbox_list[child_idx])

            children_anot.append({'id' : post_frame_ids[child_idx],
                                'Frame' : current_frame,
                                'bbox' : post_bbox_list[child_idx],
                                'near_ids' : near_ids,
                                'company' : company,
                                'warning' : warning,
                                "clothes" : clothes
                                    })

    total_annotations += annotations
    total_children += children_anot
    display(pd.DataFrame(children_anot)) ###출력###
    return post_frame_ids, post_frame_vecs, post_centers, red_bboxes, annotations

# Inferecne

In [ ]:
from pandas.io.sql import PandasSQL
import cv2
from google.colab.patches import cv2_imshow

# 동영상 파일 열기
video_path = '/content/2021-09-08_16-18-00_wed_sunny_out_sa-bt_C0091.mp4'
cap = cv2.VideoCapture(video_path)
# 동영상 파일의 프레임 너비와 높이 가져오기
frame_width = int(cap.get(3))
frame_height = int(cap.get(4))
# VideoWriter 객체 생성
output_path = '/'.join(video_path.split('/')[:-2])+'/'+video_path.split('/')[-1]
print(output_path)
fourcc = cv2.VideoWriter_fourcc(*'XVID')
out = cv2.VideoWriter(output_path, fourcc, 3.0, (frame_width, frame_height))
f = 0
pre_frame_ids = []
pre_frame_vecs = torch.Tensor([])
pre_centers = []
person_num = 0
total_children = []

while cap.isOpened():
    try:
        f += 1
        ret, frame = cap.read()
        if not ret:
            break

        post_bbox_list, crop_list, child_list = stage_1(model_1, frame)
        df_1, post_frame_vecs, output = stage_2(model_2, crop_list)

        pre_frame_ids, pre_frame_vecs, pre_centers, red_bboxes, annotations = tracking(pre_frame_ids,
                                                            pre_frame_vecs,
                                                            pre_centers,
                                                            post_bbox_list,
                                                            post_frame_vecs,
                                                            (f-1),
                                                            output,
                                                            child_list,
                                                            distance_rate=0.8,
                                                            speed_threshold = 0)

        anno_list = annotations
        if len(anno_list):
            # 사각형 그리기
            for anno in anno_list:
                start_point = (anno['bbox'][0], anno['bbox'][1])  # 사각형 시작점
                end_point = (anno['bbox'][2], anno['bbox'][3])    # 사각형 끝점
                if anno['bbox'] in red_bboxes :
                    color = (0, 0, 255)
                else:
                    color = (0, 255, 0)       # 사각형 색상 (BGR)
                thickness = 2             # 선 두께
                font_scale = 0.5
                font = cv2.FONT_HERSHEY_SIMPLEX
                frame = cv2.rectangle(frame, start_point, end_point, color, thickness)
                frame = cv2.putText(frame, anno['id'], end_point, font, font_scale, color, thickness)
        out.write(frame)
        #cv2_imshow(frame)
        save_file = f'/content/drive/MyDrive/Object_Detection/showing_img3/2021-09-08_16-18-00_wed_sunny_out_sa-bt_C0091_F{f}.jpg'
        cv2.imwrite(save_file, frame)

    except:
        continue

cap.release()
out.release()
cv2.destroyAllWindows()

/2021-09-08_16-18-00_wed_sunny_out_sa-bt_C0091.mp4


Empty DataFrame
Columns: []
Index: []

Empty DataFrame
Columns: []
Index: []

Empty DataFrame
Columns: []
Index: []

Empty DataFrame
Columns: []
Index: []

...

Empty DataFrame
Columns: []
Index: []

Empty DataFrame
Columns: []
Index: []

Empty DataFrame
Columns: []
Index: []

Empty DataFrame
Columns: []
Index: []

Empty DataFrame
Columns: []
Index: []

In [ ]:
pd.DataFrame(total_annotations[-20:])

id  Frame                  bbox         speed  \
0   Person_95    488   (790, 59, 808, 107)  [-1.0, -3.0]   
1   Person_95    489   (788, 59, 806, 104)  [-2.0, -3.0]   
2   Person_95    490   (785, 58, 804, 106)   [-2.5, 2.0]   
3   Person_95    491   (782, 56, 802, 103)  [-2.5, -3.0]   
4   Person_95    492   (790, 58, 812, 102)   [9.0, -1.0]   
5   Person_95    492   (782, 56, 803, 101)   [0.5, -2.0]   
6   Person_95    493    (779, 54, 806, 96)   [0.0, -5.0]   
7   Person_95    493   (798, 58, 817, 101)   [6.5, -1.0]   
8   Person_95    494   (800, 58, 818, 101)    [1.5, 0.0]   
9   Person_95    494    (774, 53, 792, 90)  [-9.5, -6.0]   
10  Person_95    495   (802, 60, 820, 104)    [2.0, 3.0]   
11  Person_95    495    (780, 52, 805, 95)    [9.5, 5.0]   
12  Person_95    496   (803, 59, 822, 105)    [1.5, 1.0]   
13  Person_95    497   (802, 59, 820, 104)  [-1.5, -1.0]   
14  Person_98    497    (781, 51, 802, 94)        [0, 0]   
15  Person_95    501   (800, 61, 821, 108)   [-0.5, 4.0]   
16  Person_95    502   (801, 62, 822, 109)    [1.0, 1.0]   
17  Person_99    506  (679, 247, 715, 347)        [0, 0]   
18  Person_99    507  (680, 248, 715, 348)    [0.5, 1.0]   
19  Person_99    508  (679, 248, 715, 348)   [-0.5, 0.0]   

                                      clothes  
0    [short_sleeve, black, long_pants, black]  
1    [short_sleeve, black, long_pants, black]  
2    [short_sleeve, black, long_pants, black]  
3    [short_sleeve, black, long_pants, black]  
4        [short_sleeve, red, long_pants, red]  
5   [short_sleeve, black, short_pants, black]  
6      [short_sleeve, red, long_pants, black]  
7    [short_sleeve, black, long_pants, black]  
8      [long_sleeve, grey, long_pants, black]  
9        [short_sleeve, red, long_pants, red]  
10     [long_sleeve, grey, long_pants, black]  
11     [short_sleeve, black, long_pants, red]  
12     [short_sleeve, red, long_pants, black]  
13     [long_sleeve, grey, long_pants, black]  
14    [short_sleeve, black, long_pants, blue]  
15     [short_sleeve, red, long_pants, black]  
16     [short_sleeve, red, long_pants, black]  
17     [short_sleeve, red, long_pants, black]  
18     [short_sleeve, red, long_pants, black]  
19     [short_sleeve, red, long_pants, black]

In [ ]:
pd.DataFrame(total_children[-10:])

id  Frame                   bbox                near_ids  \
0  Person_57    259  (843, 812, 950, 1062)  [Person_65, Person_82]   
1  Person_65    260  (642, 860, 740, 1079)  [Person_57, Person_82]   
2  Person_57    260  (853, 842, 958, 1073)  [Person_65, Person_82]   
3  Person_82    260  (761, 842, 863, 1071)  [Person_65, Person_57]   
4  Person_57    261  (861, 872, 971, 1072)  [Person_65, Person_82]   
5  Person_65    261  (640, 888, 743, 1076)  [Person_57, Person_82]   
6  Person_82    261  (770, 861, 868, 1075)  [Person_57, Person_65]   
7  Person_57    262  (860, 882, 984, 1074)             [Person_82]   
8  Person_82    262  (756, 870, 857, 1078)             [Person_57]   
9  Person_82    263  (739, 885, 835, 1076)                      []   

                  company  warning                                   clothes  
0  [Person_65, Person_82]        0  [short_sleeve, white, long_pants, black]  
1  [Person_57, Person_82]        0  [short_sleeve, black, short_pants, blue]  
2  [Person_65, Person_82]        0  [short_sleeve, white, long_pants, black]  
3  [Person_65, Person_57]        0  [short_sleeve, green, long_pants, black]  
4  [Person_65, Person_82]        0  [short_sleeve, white, long_pants, black]  
5             [Person_57]        0   [short_sleeve, red, short_pants, black]  
6             [Person_57]        0  [short_sleeve, green, long_pants, black]  
7                      []        1  [short_sleeve, white, long_pants, black]  
8                      []        1    [short_sleeve, red, long_pants, black]  
9                      []        1    [short_sleeve, red, long_pants, black]

# Serving

## Flask

In [ ]:
import io
import os

import cv2
import flask
from flask import Flask, send_file, request, Response, render_template, send_from_directory, jsonify
from flask_cors import CORS, cross_origin
import numpy as np
import tensorflow as tf
from PIL import ImageFile

app = flask.Flask(__name__)
app.config['MAX_CONTENT_LENGTH'] = 1000 * 1024 * 1024  # 100MB
app.config['CORS_HEADERS'] = 'Content-Type'
cors = CORS(app)
image_folder = 'static/img/1'

def find_image_files(folder):
    image_files = []
    for filename in os.listdir(folder):
        if filename.lower().endswith('.jpg'):
            image_files.append(filename)
    return image_files

@app.route('/img/<path:filename>')
def serve_image(filename):
    return send_from_directory(image_folder, filename)

@cross_origin()
@app.route("/", methods=['GET', 'POST'])
def index():
    image_files = find_image_files(image_folder)

    if request.method == 'POST':
        new_index = int(request.form.get('new_index'))
        return jsonify({"message": "인덱스 변경 성공"})

    return render_template('index.html', image_files=image_files, output_source=output_source2)

if __name__ == "__main__":
    print(("* Flask starting server..."
        "please wait until server has fully started"))

    app.run(host='0.0.0.0', port='8081')

## index.html

In [ ]:
<!doctype html>
<html lang="ko">

<head>
    <meta charset="utf-8">
    <meta name="viewport" content="width=device-width, initial-scale=1">
    <link href="https://cdn.jsdelivr.net/npm/bootstrap@5.3.0/dist/css/bootstrap.min.css" rel="stylesheet"
        integrity="sha384-9ndCyUaIbzAi2FUVXJi0CjmCapSmO7SnpJef0486qhLnuZ2cdeRhO02iuK6FUUVM" crossorigin="anonymous">
    <script src="https://ajax.googleapis.com/ajax/libs/jquery/3.7.0/jquery.min.js"></script>

    <style>
        .slider-container {
        text-align: center;
        }

        #slider-image {
        max-width: 100%;
        height: auto;
        margin-bottom: 20px;
        }

        #image-slider {
        width: 80%;
        }
    </style>
</head>

<body>
    <div class="container">
        <div class="row">
            <div class="col-12 slider-container">
                <img id="slider-image" src="">
                <input type="range" class="form-range" id="image-slider" min="0" max="{{ image_files|length - 1 }}" value="0">
            </div>
            <div class="col-12">
                <p id="output-source">{{ output_source[0] }}</p>
            </div>
        </div>
    </div>
    <script>
        const sliderImage = document.getElementById('slider-image');
        const imageSlider = document.getElementById('image-slider');
        const outputSourceElement = document.getElementById('output-source');
        const imageFiles = {{ image_files|tojson }};
        const outputSource = {{ output_source|tojson }};

        function updateSliderImage() {
            sliderImage.src = '/img/' + imageFiles[imageSlider.value];
            outputSourceElement.textContent = outputSource[imageSlider.value]
        }

        updateSliderImage();

        imageSlider.addEventListener('input', () => {
            updateSliderImage();
        });


        imageSlider.addEventListener('change', () => {
            const new_index = imageSlider.value;
            fetch('/', {
                method: 'POST',
                body: new URLSearchParams({
                    new_index: new_index
                }),
                headers: {
                    'Content-Type': 'application/x-www-form-urlencoded'
                }
            })
            .then(response => response.json())
            .then(data => {
                console.log(data.message);
            })
            .catch(error => console.error('Error:', error));
        });
    </script>
    <script src="https://cdn.jsdelivr.net/npm/bootstrap@5.3.0/dist/js/bootstrap.bundle.min.js"
        integrity="sha384-geWF76RCwLtnZ8qwWowPQNguL3RmwHVBC9FhGdlKrxdiJJigb/j/68SIy3Te4Bkz"
        crossorigin="anonymous"></script>
</body>

</html>